# Importing the necessary packages & libraries

In [40]:
import pandas as pd
import numpy as np
import sklearn
import ast
import validators
import string
import demoji
import pyLDAvis.sklearn
import re
import nltk

from sklearn.model_selection import train_test_split
from nltk.corpus import stopwords
from sklearn.decomposition import LatentDirichletAllocation
from sklearn.feature_extraction.text import CountVectorizer
from nltk.stem import WordNetLemmatizer
from sklearn.model_selection import GridSearchCV
from nltk import pos_tag

import warnings
warnings.filterwarnings("ignore", category=DeprecationWarning)

# Load the dataset

In [26]:
df = pd.read_csv('./translated_dataframe.csv')

In [27]:
df.head()

id      conversation_id  \
0  1598103832080584704  1598103832080584704   
1  1598103601507102720  1598103597388279808   
2  1598103593634369536  1598103593634369536   
3  1598103115060084736  1598103115060084736   
4  1598102468243599361  1598102468243599360   

                                          created_at        date      time  \
0  2022-12-01 07:56:59 Malay Peninsula Standard Time  2022-12-01  07:56:59   
1  2022-12-01 07:56:04 Malay Peninsula Standard Time  2022-12-01  07:56:04   
2  2022-12-01 07:56:02 Malay Peninsula Standard Time  2022-12-01  07:56:02   
3  2022-12-01 07:54:08 Malay Peninsula Standard Time  2022-12-01  07:54:08   
4  2022-12-01 07:51:34 Malay Peninsula Standard Time  2022-12-01  07:51:34   

               user_id  \
0  1582818998324178944   
1  1454189325432901640   
2            118166119   
3            141730376   
4           4034337795   

                                                                                                                                                                                                                                     tweet  \
0                                                                                                                                                                           Twitterのフォロワーを増やしたい。最低でも1万人。 #ChatGPT  https://t.co/78BaGH28Vs   
1                                                                           Overall, using AI to create art can expand the boundaries of creativity and allow artists to explore new directions in their work.  🧵4/4   @OpenAI #ChatGPT  👀   
2                   Este prompt fue creado con #ChatGPT el nuevo modelo de chat de @OpenAI  🤯, el siguiente #MartesDeDatos en @platzi hablaremos de  #ChatGPT y text-davinci-003 los nuevos modelos para GPT3. 💚🚀  https://t.co/2cZVInL9bD   
3  Just played around with OpenAI's new #ChatGPT model and asked it to write a poem about embodied carbon in buildings. This is what I got...   Try out ChatGPT  https://t.co/vaov2Ttluo  #embodiedcarbon #poetry  https://t.co/DbgO6Qz2Zq   
4                                                                                                                                     I asked #ChatGPT to write me a story about Sova and Jett falling in love...  https://t.co/yyZNrFRTQs   

  language                                 hashtags reply_to  \
0       ja                              ['chatgpt']       []   
1       en                              ['chatgpt']       []   
2       es  ['chatgpt', 'martesdedatos', 'chatgpt']       []   
3       en  ['chatgpt', 'embodiedcarbon', 'poetry']       []   
4       en                              ['chatgpt']       []   

                                                                                                                                                                                                                           translated_text  \
0                                                                                                                                               I want to increase my Twitter followers. At least 10,000. #ChatGPT https://t.co/78BaGH28Vs   
1                                                                           Overall, using AI to create art can expand the boundaries of creativity and allow artists to explore new directions in their work.  🧵4/4   @OpenAI #ChatGPT  👀   
2                         This prompt was created with #ChatGPT the new @OpenAI 🤯 chat model, the following #MartesDeDatos in @platzi we will talk about #ChatGPT and text-davinci-003 the new models for GPT3. 💚🚀 https://t.co/2cZVInL9bD   
3  Just played around with OpenAI's new #ChatGPT model and asked it to write a poem about embodied carbon in buildings. This is what I got...   Try out ChatGPT  https://t.co/vaov2Ttluo  #embodiedcarbon #poetry  https://t.co/DbgO6Qz2Zq   
4                                                                                                          

# Converting the dataframe to Documents

In [28]:
def DFToDocument(df):
    document = []
    lemmatizer = WordNetLemmatizer()
    stop_words = set(stopwords.words('english'))
    for i, row in df.iterrows():
        sentence = ""
        tokenized_text = ast.literal_eval(row['tokenized_text'])
        pos_tags = pos_tag(tokenized_text)
        tonkenized_text = [token for token, pos in pos_tags if pos not in ['JJ', 'JJR', 'JJS', 'RB', 'RBR', 'RBS', 'VB']]
        for token in tokenized_text:
            if token not in stop_words and not validators.url(token) and token not in string.punctuation and not re.search(r'(chat[-\s])?gpt|\d+', token.lower()):
                sentence += lemmatizer.lemmatize(token) + ' '
        sentence = demoji.replace(string = sentence, repl = "")
        document.append(sentence[:-1])
    return document

In [29]:
document = DFToDocument(df)

# Split the data into training and testing data
70% Training Data <br><br>
30% Testing Data

In [30]:
chatgpt_train, chatgpt_test = train_test_split(document, test_size=0.3, random_state=1)

# Utilizing Gensim & preprocess2.py file 

In [31]:
import preprocess2

chatgpt_docs_train = []

for sentence in chatgpt_train:
    tokenized_sentence = nltk.word_tokenize(sentence)
    chatgpt_docs_train.append(tokenized_sentence)

chatgpt_docs_test = []

for sentence in chatgpt_test:
    tokenized_sentence = nltk.word_tokenize(sentence)
    chatgpt_docs_test.append(tokenized_sentence)


In [32]:
import gensim
import preprocess2

chatgpt_dictionary_train = gensim.corpora.Dictionary(chatgpt_docs_train)
chatgpt_dictionary_test = gensim.corpora.Dictionary(chatgpt_docs_test)

chatgpt_vecs_train = preprocess2.docs2vecs(chatgpt_docs_train, chatgpt_dictionary_train)
chatgpt_vecs_test = preprocess2.docs2vecs(chatgpt_docs_test, chatgpt_dictionary_test)


# Fitting the training data into the LDA model

In [36]:
chatgpt_lda = gensim.models.ldamodel.LdaModel(
                                        corpus=chatgpt_vecs_train, 
                                        id2word=chatgpt_dictionary_train, 
                                        num_topics=6)

In [10]:
topics = chatgpt_lda.show_topics(6, 5)

for i in range(0, 6):
    print(topics[i])

(0, '0.086*"#" + 0.023*"AI" + 0.014*"Google" + 0.010*"Bing" + 0.009*"I"')
(1, '0.060*"#" + 0.026*"AI" + 0.016*"\'s" + 0.012*"I" + 0.007*"The"')
(2, '0.225*"#" + 0.036*"AI" + 0.009*"OpenAI" + 0.008*"\'s" + 0.008*"I"')
(3, '0.142*"#" + 0.025*"I" + 0.018*"The" + 0.016*"AI" + 0.010*"’"')
(4, '0.056*"I" + 0.017*"It" + 0.015*"..." + 0.013*"\'s" + 0.013*"use"')
(5, '0.057*"I" + 0.014*"like" + 0.010*"asked" + 0.010*"answer" + 0.010*"#"')


In [11]:
import pyLDAvis
import pyLDAvis.gensim_models as gensimvis
pyLDAvis.enable_notebook()

In [12]:
# Generate the visuals
visual= gensimvis.prepare(chatgpt_lda, chatgpt_vecs_train, chatgpt_dictionary_train)

/home/jupyter/.local/lib/python3.9/site-packages/pyLDAvis/_prepare.py:243: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.
  default_term_info = default_term_info.sort_values(


In [13]:
# Save the output to the html file
pyLDAvis.save_html(visual, "topic_viz_gensim_v2_AED.html")

# Evaluating the Perplexity for the LDA Model

In [14]:
# Compute Perplexity
perplex= chatgpt_lda.log_perplexity(chatgpt_vecs_test, total_docs=None) 

In [15]:
print('\nPerplexity for LDAModel: ', perplex)


Perplexity for LDAModel:  -12.675121493833272


# Evaluating the Coherence for the LDA Model

In [16]:
from gensim.models import CoherenceModel

coherence_model_lda = CoherenceModel(model=chatgpt_lda, 
                                     texts=chatgpt_docs_test, 
                                     dictionary=chatgpt_dictionary_test, 
                                     coherence='c_v')

coherence_lda = coherence_model_lda.get_coherence()
print('\nCoherence Score LDAModel: ', coherence_lda)


Coherence Score LDAModel:  0.5630128554206548


In [17]:
# Can take a long time to run. In this case we are going to  k_max=10.
import datetime
print(datetime.datetime.now())

from gensim.models import CoherenceModel

model_list = []
coherence_values = []
model_topics = []

for num_topics in range(2, 10, 2):
    chatgpt_lda_x = gensim.models.ldamodel.LdaModel(corpus=chatgpt_vecs_train, id2word=chatgpt_dictionary_train, num_topics=num_topics)
    coherencemodel = CoherenceModel(model=chatgpt_lda_x, texts=chatgpt_docs_test, dictionary=chatgpt_dictionary_test, coherence='c_v')
    model_topics.append(num_topics)
    model_list.append(chatgpt_lda_x)
    coherence_values.append(coherencemodel.get_coherence())
    print("#Topics: " + str(num_topics) + " Score: " + str(coherencemodel.get_coherence()))

print(datetime.datetime.now())

2023-04-11 13:47:23.235428
#Topics: 2 Score: 0.5541205947070846
#Topics: 4 Score: 0.5627997507530351
#Topics: 6 Score: 0.5929353270826075
#Topics: 8 Score: 0.6298302675033745
2023-04-11 13:47:37.157174


### Ploting the results of the Coherence Score (Y-axis) against the Number of Topics (X-Axis)

In [18]:
# Show graph

import matplotlib.pyplot as plt

limit=10; start=2; step=2;
x = range(start, limit, step)
plt.plot(x, coherence_values)
plt.xlabel("Num Topics")
plt.ylabel("Coherence score")
plt.legend(("coherence_values"), loc='best')
plt.show()

# Insights: The graph is aligned with our clustering results

In [19]:
# Print the coherence scores
for m, cv in zip(x, coherence_values):
    print("Num Topics =", m, " has Coherence Value of", round(cv, 4))

Num Topics = 2  has Coherence Value of 0.5541
Num Topics = 4  has Coherence Value of 0.5628
Num Topics = 6  has Coherence Value of 0.5929
Num Topics = 8  has Coherence Value of 0.6298


# Finding the most dominant topic among the dataset

In [20]:
#Find most dominant topic

import numpy as np
import pandas as pd

def format_topics_sentences(ldamodel, corpus, data):
    # Init output
    sent_topics_df = pd.DataFrame()

    # Get main topic in each document
    for i, row in enumerate(ldamodel[corpus]):
        row = sorted(row, key=lambda x: (x[1]), reverse=True)
        # Get the Dominant topic, Perc Contribution and Keywords for each document
        for j, (topic_num, prop_topic) in enumerate(row):
            if j == 0:  # => dominant topic
                wp = ldamodel.show_topic(topic_num)
                topic_keywords = ", ".join([word for word, prop in wp])
                sent_topics_df = sent_topics_df.append(pd.Series([int(topic_num), round(prop_topic,4), topic_keywords]), ignore_index=True)
            else:
                break
    sent_topics_df.columns = ['Dominant_Topic', 'Perc_Contribution', 'Topic_Keywords']

    # Add original text to the end of the output
    contents = pd.Series(data)
    sent_topics_df = pd.concat([sent_topics_df, contents], axis=1)
    return(sent_topics_df)

#I choose model_list[2] where the number of topics is 6

df_topic_sents_keywords = format_topics_sentences(ldamodel=model_list[2], corpus=chatgpt_vecs_train, data=chatgpt_docs_train)

# Format
df_dominant_topic = df_topic_sents_keywords.reset_index()
df_dominant_topic.columns = ['Document_No', 'Dominant_Topic', 'Topic_Percentage_Contribution', 'Keywords', 'Text']

# Show
pd.set_option("display.max_colwidth", None)
df_dominant_topic.head(6)

/tmp/ipykernel_85547/3348815634.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  sent_topics_df = sent_topics_df.append(pd.Series([int(topic_num), round(prop_topic,4), topic_keywords]), ignore_index=True)
/tmp/ipykernel_85547/3348815634.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  sent_topics_df = sent_topics_df.append(pd.Series([int(topic_num), round(prop_topic,4), topic_keywords]), ignore_index=True)
/tmp/ipykernel_85547/3348815634.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  sent_topics_df = sent_topics_df.append(pd.Series([int(topic_num), round(prop_topic,4), topic_keywords]), ignore_index=True)
/tmp/ipykernel_85547/3348815634.py:18: FutureWarning: The frame.append method is deprecated and will be re

Document_No  Dominant_Topic  Topic_Percentage_Contribution  \
0            0               0                         0.7449   
1            1               4                         0.8792   
2            2               0                         0.1667   
3            3               5                         0.6918   
4            4               4                         0.6021   
5            5               5                         0.7892   

                                                                     Keywords  \
0  #, AI, ai, openai, Google, artificialintelligence, via, How, chatbot, What   
1                        I, ..., like, 's, asked, answer, think, 'm, AI, know   
2  #, AI, ai, openai, Google, artificialintelligence, via, How, chatbot, What   
3                         AI, I, The, new, 's, It, #, Bing, Microsoft, search   
4                        I, ..., like, 's, asked, answer, think, 'm, AI, know   
5                         AI, I, The, new, 's, It, #, Bing, Microsoft, search   

                                                                                                                                                                                                                                               Text  
0                                                                                                                                                                                                                               [More, #, ExoSquad]  
1  [I, 'm, exploring, using, get, way, help, #, teaching, lot, task, asked, #, faculty, day, take, needed, necessary, time, teaching, researching, appropriaterelevant, meaningful, tech, ARMtech, help, effectivity, quality, might, I, use, tech]  
2                                                                                                                                                                                                                                                []  
3                                                                   [Good, morning, When, I, woke, morning, open, PLUS, member, Today, World, Expo, Day, day, think, future, No, evolve, dramatically, ️, What, Expo, Day, #, トレンドキーワード解説, #, 万博デー]  
4                                                                                                                                                                                                                                      [using, igl]  
5                                           [Could, n't, agree, building, new, approach, break, browsing, unproductive, habit, exciting, thing, Me, team, working, web, extension, plugging, website, facilitating, effective, prompt, engineering]

# Saving the models

In [21]:
#Save a model to disk, or reload a pre-trained model
chatgpt_lda_sav = model_list[2] #Or you can save the best model, model_list[1]

chatgpt_lda_sav.save("LDAmodel_Topics_Gensim_V2_AED")

lda_disk = gensim.models.ldamodel.LdaModel.load("LDAmodel_Topics_Gensim_V2_AED")

In [22]:
#Code to save the document topic probabilities (theta)
import pandas as pd

vec = chatgpt_lda_sav[chatgpt_vecs_train]
pd.DataFrame(vec).to_csv("doc_topic_mixture_AED.csv")

In [23]:
# Write code here to save top 10 words for each topic (beta)
top_words_per_topic = []

for t in range(chatgpt_lda_sav.num_topics):
    top_words_per_topic.extend([(t, ) + x for x in chatgpt_lda_sav.show_topic(t, topn = 10)])

pd.DataFrame(top_words_per_topic, columns=['Topic', 'Word', 'P']).to_csv("top_words_gensim_v2_AED.csv")

In [24]:
# END OF GENSIM V2 LDA